In [1]:
import feedparser
import os.path
import sys, getopt
import time
import socket
from urllib.request import urlopen
from urllib.error import URLError, HTTPError
import xml.etree.ElementTree as ET
import zipfile
import zlib

In [2]:
EXT_DIR = "/media/reggie/reg_ext/EDGAR/xbrl/"
EXT_DIR = "/home/reggie/EDGAR/xbrl/"

## Download XBRL Filings
We need to download the XBRL RSS feed from EDGAR, which contains an XML file of all the XBRL files uploaded to EDGAR in a given month.

In [3]:
## A general file download utility function
def downloadfile( sourceurl, targetfname ):
    mem_file = ""
    good_read = False
    xbrlfile = None
    if os.path.isfile( targetfname ):
        print( "Local copy already exists" )
        return True
    else:
        print( "Downloading:", sourceurl )
        try:
            xbrlfile = urlopen( sourceurl )
            try:
                mem_file = xbrlfile.read()
                good_read = True
            finally:
                xbrlfile.close()
        except HTTPError as e:
            print( "HTTP Error:", e.code )
        except URLError as e:
            print( "URL Error:", e.reason )
        except TimeoutError as e:
            print( "Timeout Error:", e.reason )
        except socket.timeout:
            print( "Socket Timeout Error" )
        if good_read:
            output = open( targetfname, 'wb' )
            output.write( mem_file )
            output.close()
        return good_read

In [4]:
def download_xbrl_zipfile(item, enclosures, target_dir):
    enclosure = enclosures[0]
    sourceurl = enclosure[ "href" ]
    cik = item[ "edgar_ciknumber" ]
    targetfname = target_dir+cik+'-'+sourceurl.split('/')[-1]
    retry_counter = 3
    while retry_counter > 0:
        good_read = downloadfile( sourceurl, targetfname )
        if good_read:
            break
        else:
            print( "Retrying:", retry_counter )
            retry_counter -= 1

In [5]:
def download_xbrl_manually(root, item, target_dir, itemIndex):
    """
    item:
    target_dir:
    itemIndex:
    """
    linkname = item[ "link" ].split('/')[-1]
    linkbase = os.path.splitext(linkname)[0]
    cik = item[ "edgar_ciknumber" ]
    zipfname = target_dir+cik+'-'+linkbase+"-xbrl.zip"
    if not os.path.isfile( zipfname ):
        edgarNamespace = {'edgar': 'http://www.sec.gov/Archives/edgar'}
        currentItem = list(root.iter( "item" ))[itemIndex]
        xbrlFiling = currentItem.find( "edgar:xbrlFiling", edgarNamespace )
        xbrlFilesItem = xbrlFiling.find( "edgar:xbrlFiles", edgarNamespace )
        xbrlFiles = xbrlFilesItem.findall( "edgar:xbrlFile", edgarNamespace )
        if not os.path.exists(  target_dir+"temp" ):
            os.makedirs( target_dir+"temp" )
        zf = zipfile.ZipFile( zipfname, "w" )
        try:
            for xf in xbrlFiles:
                xfurl = xf.get( "{http://www.sec.gov/Archives/edgar}url" )
                if xfurl.endswith( (".xml",".xsd") ):
                    targetfname = target_dir+"temp/"+xfurl.split('/')[-1]
                    retry_counter = 3
                    while retry_counter > 0:
                        good_read = downloadfile( xfurl, targetfname )
                        if good_read:
                            break
                        else:
                            print( "Retrying:", retry_counter )
                            retry_counter -= 1
                    zf.write( targetfname, xfurl.split('/')[-1], zipfile.ZIP_DEFLATED )
                    os.remove( targetfname )
        finally:
            zf.close()
            os.rmdir( target_dir+"temp" )

In [6]:
def sec_download(year, month, form_type="10-K"):
    root = None
    feedFile = None
    feedData = None
    good_read = False
    itemIndex = 0
    edgarFilingsFeed = 'http://www.sec.gov/Archives/edgar/monthly/xbrlrss-' + str(year) + '-' + str(month).zfill(2) + '.xml'

    target_dir = EXT_DIR + "/" + str(year) + '/' + str(month).zfill(2) + '/'
    if not os.path.exists(target_dir):
        os.makedirs(target_dir)


    feedFile = urlopen( edgarFilingsFeed )
    feedData = feedFile.read()
    feedFile.close()

    # we have to unfortunately use both feedparser (for normal cases) and ET for old-style RSS feeds,
    # because feedparser cannot handle the case where multiple xbrlFiles are referenced without enclosure
    try:
        root = ET.fromstring(feedData)
    except ET.ParseError as perr:
        print( "XML Parser Error:", perr )
    feed = feedparser.parse( feedData )
    print( feed[ "channel" ][ "title" ] )

    # Process RSS feed and walk through all items contained
    for item in feed.entries:
        try:
            print( item[ "summary" ], item[ "title" ], item[ "published" ] )

            # Identify ZIP file enclosure, if available
            enclosures = [ l for l in item[ "links" ] if l[ "rel" ] == "enclosure" ]
            if item["summary"].find(form_type) > -1:
                if ( len( enclosures ) > 0 ):
                    # ZIP file enclosure exists, so we can just download the ZIP file
                    download_xbrl_zipfile(item, enclosures, target_dir)
                else:
                    # We need to manually download all XBRL files here and ZIP them ourselves...
                    download_xbrl_manually(root, item, target_dir, itemIndex)
        except KeyError as e:
            print( "Key Error:", e )
        finally:
            print( "----------" )
        itemIndex += 1

In [7]:
for year in range(2011,2019):
    for quarter in range(1,5):
        sec_download(year, quarter, "10-K")

All XBRL Data Submitted to the SEC for 2011-01
10-Q INTERNATIONAL RECTIFIER CORP /DE/ (0000316793) (Filer) Mon, 31 Jan 2011 17:20:59 EST
----------
10-K PROGRESS SOFTWARE CORP /MA (0000876167) (Filer) Mon, 31 Jan 2011 17:10:25 EST
Local copy already exists
----------
10-K KB HOME (0000795266) (Filer) Mon, 31 Jan 2011 16:45:12 EST
Local copy already exists
----------
10-K LENNAR CORP /NEW/ (0000920760) (Filer) Mon, 31 Jan 2011 16:43:34 EST
Local copy already exists
----------
10-K TEMPUR PEDIC INTERNATIONAL INC (0001206264) (Filer) Mon, 31 Jan 2011 16:22:00 EST
Local copy already exists
----------
10-K AMERON INTERNATIONAL CORP (0000790730) (Filer) Mon, 31 Jan 2011 16:17:09 EST
Local copy already exists
----------
10-Q JOHNSON CONTROLS INC (0000053669) (Filer) Mon, 31 Jan 2011 14:41:17 EST
----------
485BPOS PRUDENTIAL INVESTMENT PORTFOLIOS 11 (0000355605) (Filer) Mon, 31 Jan 2011 12:38:39 EST
----------
10-K CARNIVAL CORP (0000815097) (Filer) Mon, 31 Jan 2011 09:35:28 EST
Local copy al

All XBRL Data Submitted to the SEC for 2011-02
10-K CHIMERA INVESTMENT CORP (0001409493) (Filer) Mon, 28 Feb 2011 17:29:19 EST
Local copy already exists
----------
10-K Interactive Brokers Group, Inc. (0001381197) (Filer) Mon, 28 Feb 2011 17:28:45 EST
Local copy already exists
----------
10-K Brookdale Senior Living Inc. (0001332349) (Filer) Mon, 28 Feb 2011 17:27:50 EST
Local copy already exists
----------
10-K WEST PHARMACEUTICAL SERVICES INC (0000105770) (Filer) Mon, 28 Feb 2011 17:27:31 EST
Local copy already exists
----------
10-K Valeant Pharmaceuticals International, Inc. (0000885590) (Filer) Mon, 28 Feb 2011 17:27:02 EST
Local copy already exists
----------
10-K ORMAT TECHNOLOGIES, INC. (0001296445) (Filer) Mon, 28 Feb 2011 17:26:29 EST
Local copy already exists
----------
10-K ILLUMINA INC (0001110803) (Filer) Mon, 28 Feb 2011 17:26:26 EST
Local copy already exists
----------
10-K GREENHILL & CO INC (0001282977) (Filer) Mon, 28 Feb 2011 17:23:02 EST
Local copy already exists
-

Local copy already exists
----------
10-K CHICAGO BRIDGE & IRON CO N V (0001027884) (Filer) Tue, 22 Feb 2011 17:21:15 EST
Local copy already exists
----------
10-K STILLWATER MINING CO /DE/ (0000931948) (Filer) Tue, 22 Feb 2011 17:19:41 EST
Local copy already exists
----------
10-K STRAYER EDUCATION INC (0001013934) (Filer) Tue, 22 Feb 2011 17:16:32 EST
Local copy already exists
----------
10-K PAPA JOHNS INTERNATIONAL INC (0000901491) (Filer) Tue, 22 Feb 2011 17:15:53 EST
Local copy already exists
----------
10-K CATERPILLAR INC (0000018230) (Filer) Tue, 22 Feb 2011 17:15:14 EST
Local copy already exists
----------
10-K Cooper Industries plc (0001141982) (Filer) Tue, 22 Feb 2011 17:10:07 EST
Local copy already exists
----------
10-K TrueBlue, Inc. (0000768899) (Filer) Tue, 22 Feb 2011 17:05:29 EST
Local copy already exists
----------
10-K TUPPERWARE BRANDS CORP (0001008654) (Filer) Tue, 22 Feb 2011 17:05:07 EST
Local copy already exists
----------
10-K NEW YORK TIMES CO (0000071691) (

All XBRL Data Submitted to the SEC for 2011-03
10-K/A BMX Development Corp. (0001314054) (Filer) Thu, 31 Mar 2011 17:17:36 EDT
Local copy already exists
----------
10-K WILLIAMS SONOMA INC (0000719955) (Filer) Thu, 31 Mar 2011 17:06:31 EDT
Local copy already exists
----------
8-K PEPSICO INC (0000077476) (Filer) Thu, 31 Mar 2011 16:36:06 EDT
----------
10-Q SCHOLASTIC CORP (0000866729) (Filer) Thu, 31 Mar 2011 16:14:24 EDT
----------
10-K SEMTECH CORP (0000088941) (Filer) Thu, 31 Mar 2011 16:08:53 EDT
Local copy already exists
----------
40-F BARRICK GOLD CORP (0000756894) (Filer) Thu, 31 Mar 2011 15:55:26 EDT
----------
485BPOS JPMorgan Trust I (0001217286) (Filer) Thu, 31 Mar 2011 14:55:56 EDT
----------
485BPOS ARCHER INVESTMENT SERIES TRUST (0001477491) (Filer) Thu, 31 Mar 2011 14:40:46 EDT
----------
497 FIRST AMERICAN INVESTMENT FUNDS INC (0000820892) (Filer) Thu, 31 Mar 2011 14:07:08 EDT
----------
10-Q MOSAIC CO (0001285785) (Filer) Thu, 31 Mar 2011 13:57:09 EDT
----------
10-K

Local copy already exists
----------
10-K AKAMAI TECHNOLOGIES INC (0001086222) (Filer) Tue, 01 Mar 2011 12:47:11 EST
Local copy already exists
----------
10-K SOUTH CAROLINA ELECTRIC & GAS CO (0000091882) (Filer) Tue, 01 Mar 2011 12:21:27 EST
Local copy already exists
----------
10-K TEXTRON INC (0000217346) (Filer) Tue, 01 Mar 2011 12:07:14 EST
Local copy already exists
----------
10-K PERKINELMER INC (0000031791) (Filer) Tue, 01 Mar 2011 12:00:14 EST
Local copy already exists
----------
10-K MEDASSETS INC (0001254419) (Filer) Tue, 01 Mar 2011 11:53:52 EST
Local copy already exists
----------
10-K C H ROBINSON WORLDWIDE INC (0001043277) (Filer) Tue, 01 Mar 2011 11:52:53 EST
Local copy already exists
----------
10-K BEMIS CO INC (0000011199) (Filer) Tue, 01 Mar 2011 11:46:36 EST
Local copy already exists
----------
10-K CHOICE HOTELS INTERNATIONAL INC /DE (0001046311) (Filer) Tue, 01 Mar 2011 11:40:18 EST
Local copy already exists
----------
10-K ENTERPRISE PRODUCTS PARTNERS L P (00010

...

----------
10-K ABERCROMBIE & FITCH CO /DE/ (0001018840) (Filer) Mon, 27 Mar 2017 17:19:28 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1018840/000101884017000013/0001018840-17-000013-xbrl.zip
----------
10-K HINES GLOBAL REIT II, INC. (0001585101) (Filer) Mon, 27 Mar 2017 17:19:08 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1585101/000158510117000017/0001585101-17-000017-xbrl.zip
----------
S-1 NATIONWIDE LIFE INS CO (0001127203) (Filer) Mon, 27 Mar 2017 17:17:54 EDT
----------
10-K SOLIGENIX, INC. (0000812796) (Filer) Mon, 27 Mar 2017 17:17:24 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/812796/000121390017002845/0001213900-17-002845-xbrl.zip
----------
10-K 3PEA INTERNATIONAL, INC. (0001496443) (Filer) Mon, 27 Mar 2017 17:16:11 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1496443/000168316817000670/0001683168-17-000670-xbrl.zip
----------
10-K Zynerba Pharmaceuticals, Inc. (0001621443) (Filer) Mon, 27 Mar 2017 17:10:08 EDT
Downloading: ht

----------
10-K PHASERX, INC. (0001429386) (Filer) Mon, 27 Mar 2017 14:49:07 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1429386/000114420417016759/0001144204-17-016759-xbrl.zip
----------
10-K REX AMERICAN RESOURCES Corp (0000744187) (Filer) Mon, 27 Mar 2017 14:46:30 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/744187/000093041317001219/0000930413-17-001219-xbrl.zip
----------
20-F TEXTAINER GROUP HOLDINGS LTD (0001413159) (Filer) Mon, 27 Mar 2017 14:40:03 EDT
----------
10-K Oak Valley Bancorp (0001431567) (Filer) Mon, 27 Mar 2017 14:36:21 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1431567/000143774917005311/0001437749-17-005311-xbrl.zip
----------
10-Q ALL MARKETING SOLUTIONS, INC. (0001464300) (Filer) Mon, 27 Mar 2017 14:08:15 EDT
----------
10-Q Geant Corp. (0001680132) (Filer) Mon, 27 Mar 2017 13:50:19 EDT
----------
10-K GUESS INC (0000912463) (Filer) Mon, 27 Mar 2017 13:39:09 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/912463/0000

----------
10-K Wellesley Bancorp, Inc. (0001526952) (Filer) Fri, 24 Mar 2017 16:32:11 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1526952/000114420417016524/0001144204-17-016524-xbrl.zip
----------
10-K H/Cell Energy Corp (0001676580) (Filer) Fri, 24 Mar 2017 16:31:13 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1676580/000149315217002817/0001493152-17-002817-xbrl.zip
----------
10-Q SCHOLASTIC CORP (0000866729) (Filer) Fri, 24 Mar 2017 16:31:04 EDT
----------
10-K Nimble Storage Inc (0001452751) (Filer) Fri, 24 Mar 2017 16:29:10 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1452751/000119312517095656/0001193125-17-095656-xbrl.zip
----------
10-K Independence Bancshares, Inc. (0001311828) (Filer) Fri, 24 Mar 2017 16:28:58 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1311828/000120677417000970/0001206774-17-000970-xbrl.zip
----------
10-K DOLLAR GENERAL CORP (0000029534) (Filer) Fri, 24 Mar 2017 16:28:06 EDT
Downloading: http://www.sec.gov/Ar

----------
POS AM GeoVax Labs, Inc. (0000832489) (Filer) Fri, 24 Mar 2017 13:00:28 EDT
----------
10-K Federal Home Loan Bank of Boston (0001331463) (Filer) Fri, 24 Mar 2017 13:00:12 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1331463/000133146317000050/0001331463-17-000050-xbrl.zip
----------
10-K GeoVax Labs, Inc. (0000832489) (Filer) Fri, 24 Mar 2017 12:50:02 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/832489/000143774917005201/0001437749-17-005201-xbrl.zip
----------
10-K Strategic Realty Trust, Inc. (0001446371) (Filer) Fri, 24 Mar 2017 12:46:30 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1446371/000144637117000026/0001446371-17-000026-xbrl.zip
----------
10-K GUARANTY FEDERAL BANCSHARES INC (0001046203) (Filer) Fri, 24 Mar 2017 12:37:12 EDT
Downloading: http://www.sec.gov/Archives/edgar/data/1046203/000143774917005197/0001437749-17-005197-xbrl.zip
----------
10-K PERMA FIX ENVIRONMENTAL SERVICES INC (0000891532) (Filer) Fri, 24 Mar 2017 12:22:3

KeyboardInterrupt: 